# Reading and writing
or more explicitly:
# Reading and writing datasets and metadata

This tutorial shows how `xsnow` handles data I/O and metadata:

1) Read datasets
2) Inspect dimensions, coordinates, and variables
3) View and edit metadata
4) Write datasets to file

`xsnow` focuses on parsing SNOWPACK (PRO/SMET) and CROCUS (NetCDF) and will provide basic readers for CAAML/JSON. It also supports an efficient xsnow NetCDF format for caching large datasets.

- **SNOWPACK**: native PRO and SMET
- **CROCUS**: NetCDF *(planned)*
- **CAAML**: XML/JSON *(planned)*
- **xsnow NetCDF**: optimized for `xsnow`’s data model `xsnowDataset`

```{admonition} Sample datasets
:class: note

`xsnow` ships several sample datasets. Two lightweight ones are available via `xsnow.single_profile()` and `xsnow.single_profile_timeseries()`. More datasets live in [`xsnow.sample_data`](../api/_generated/xsnow.sample_data) (see API docs).
```

```{admonition} Quick overview over relevant functions
:class: note

| Task | Function/Method |
|---------|---------|
| Read any file into `xsnowDataset` | `read()` |
| Write `xsnowDataset` to file | `.to_netcdf()`, `.to_pro()`, `to_smet()` |
| Append new timesteps from files | `.append_latest()` |
| Merge SMET files | `.merge_smet()` |

```

## 1. Reading example SNOWPACK datasets
For this SNOWPACK section, we use a sample dataset of gridded simulations shipped in native SNOWPACK formats. Get the sample data path:

In [1]:
import xsnow
datapath = xsnow.sample_data.snp_gridded_dir()

The function returns a directory path. Its structure looks like:

In [2]:
# cell hidden through metadata
import os
print(f"Data location: {datapath}")
for root, dirs, files in os.walk(datapath):
    level = root.replace(datapath, "").count(os.sep)
    indent = " " * 4 * level
    print(f"{indent}{os.path.basename(root)}/")
    subindent = " " * 4 * (level + 1)
    fcounter = 0
    for f in sorted(files):
        if fcounter < 3 or fcounter > len(files)-3:
            print(f"{subindent}{f}")
        elif fcounter == 3:
            print(f"{subindent}...")
        fcounter += 1


Data location: /home/flo/.cache/xsnow-snp-gridded
xsnow-snp-gridded/
    pros/
        gridded/
            VIR1A.pro
            VIR1A.smet
            VIR1A1.pro
            ...
            VIR5A4.pro
            VIR5A4.smet
    smets/
        gridded/
            forecast/
                VIR1A.smet
                VIR2A.smet
                VIR3A.smet
                VIR4A.smet
                VIR5A.smet
            nowcast/
                VIR1A.smet
                VIR2A.smet
                VIR3A.smet
                VIR4A.smet
                VIR5A.smet


### Reading a single file
Read a single **PRO** file:

In [3]:
xs = xsnow.read(f"{datapath}/pros/gridded/VIR1A.pro")
print(xs)

[i] xsnow.xsnow_io: Loading 1 datasets eagerly with 13 workers...


<xsnowDataset>
  Locations:  1
  Timestamps: 416 (2024-01-16--2024-02-02)
  Profiles:   416 total | 416 valid | 373 with HS>0

    employing the <xarray.Dataset> Size: 545kB
    Dimensions:                   (location: 1, time: 416, slope: 1,
                                   realization: 1, layer: 12)
    Coordinates:
        altitude                  (location) float64 8B 2.372e+03
        latitude                  (location) float64 8B 47.15
      * location                  (location) <U5 20B 'VIR1A'
        longitude                 (location) float64 8B 11.19
      * time                      (time) datetime64[ns] 3kB 2024-01-16T05:00:00 ....
        azimuth                   (slope) int64 8B 0
        inclination               (slope) int64 8B 0
      * slope                     (slope) int64 8B 0
      * realization               (realization) int64 8B 0
      * layer                     (layer) int64 96B 0 1 2 3 4 5 6 7 8 9 10 11
        z                         (location, t

The summary shows 1 location and 373 timestamps. `xsnowDataset` wraps an underlying `xarray.Dataset` with additional dimensions (`slope`, `realization`, `layer`).

Read a single **SMET** file (no `layer` dimension):

In [4]:
# Read a single smet file
xs = xsnow.read(f"{datapath}/pros/gridded/VIR1A.smet")
print(xs)

<xsnowDataset>
  Locations:  1
  Timestamps: 416 (2024-01-16--2024-02-02)
  Profiles:   416 total | 0 valid | unavailable with HS>0

    employing the <xarray.Dataset> Size: 213kB
    Dimensions:               (location: 1, time: 416, slope: 1, realization: 1)
    Coordinates:
        altitude              (location) float64 8B 2.372e+03
        latitude              (location) float64 8B 47.15
      * location              (location) object 8B 'VIR1A'
        longitude             (location) float64 8B 11.19
      * time                  (time) datetime64[ns] 3kB 2024-01-16T05:00:00 ... 2...
        azimuth               (slope) float64 8B 0.0
        inclination           (slope) float64 8B 0.0
      * slope                 (slope) int64 8B 0
      * realization           (realization) int64 8B 0
    Data variables: (12/64)
        ColdContentSnow       (location, time, slope, realization) float64 3kB 0....
        DW                    (location, time, slope, realization) float64 3k

### Reading multiple files
Read multiple files by (1) passing a list of paths or (2) pointing to a directory. Files are merged on shared coordinates (e.g., `location`, `time`). Note that for parsing SNOWPACK formats, the merging is based on identical `StationName`s and `station_name`s (properties of PRO and SMET files). Therefore, please don't use the same station names for different locations.

In [5]:
# Reading a list of filepaths
xs = xsnow.read([
    f"{datapath}/pros/gridded/VIR1A.pro",            # profile data
    f"{datapath}/pros/gridded/VIR1A.smet",           # scalar output data
    f"{datapath}/smets/gridded/nowcast/VIR1A.smet",  # weather input data
])

[i] xsnow.xsnow_io: Loading 1 datasets eagerly with 13 workers...


In [6]:
# Reading all files within one directory
xs = xsnow.read(f"{datapath}/pros/gridded/")

[i] xsnow.xsnow_io: Using lazy loading with Dask
[i] xsnow.xsnow_io: Creating lazy datasets backed by dask arrays...
[i] xsnow.xsnow_io: Data will NOT be computed until explicitly requested by user
[i] xsnow.xsnow_io: Created 25 lazy datasets (data NOT yet loaded into memory)


In [7]:
print(xs)

<xsnowDataset>
  Locations:  5
  Timestamps: 416 (2024-01-16--2024-02-02)
  Profiles:   10400 total | 10400 valid | 8861 with HS>0

    employing the <xarray.Dataset> Size: 42MB
    Dimensions:                   (location: 5, time: 416, slope: 5,
                                   realization: 1, layer: 33)
    Coordinates:
        altitude                  (location) float64 40B 2.372e+03 ... 2.066e+03
        latitude                  (location) float64 40B 47.15 47.44 ... 47.44 47.37
      * location                  (location) <U5 100B 'VIR1A' 'VIR2A' ... 'VIR5A'
        longitude                 (location) float64 40B 11.19 11.29 11.3 11.39 11.5
      * time                      (time) datetime64[ns] 3kB 2024-01-16T05:00:00 ....
        azimuth                   (slope) int64 40B 0 0 90 180 270
        inclination               (slope) int64 40B 0 38 38 38 38
      * slope                     (slope) int64 40B 0 1 2 3 4
      * realization               (realization) int64 8B 0
  

### Adding SMET files to an existing dataset
Add `.smet` files to your `xsnowDataset` after reading it with `xsnowDataset.merge_smet()`. You can pass a single file, a list of files, or a directory.

In [8]:
xs = xsnow.read(f"{datapath}/pros/gridded/VIR1A.pro")
xs = xs.merge_smet(f"{datapath}/pros/gridded/VIR1A.smet")

[i] xsnow.xsnow_io: Loading 1 datasets eagerly with 13 workers...


```{tip}
Use `var_prefix` to avoid name collisions (e.g., input SMET variables as `input_TA`, `input_PSUM`, etc.).
This keeps data organized and prevents overwriting variables with identical names across input/output SMETs.
```

### Appending new timesteps from updated source files
If your simulations run operationally during a season on a day-by-day basis, you may want to append new times to the existing dataset. It is much more efficient to cache the dataset in a binary format (e.g., NetCDF) and only read new timesteps from the PRO and SMET files. The method `xsnowDataset.append_latest()` allows you to do that conveniently. Make sure you also read the dedicated section on *Updating xsnowDatasets with recent data* in the [Combining datasets](./combining_data.ipynb) tutorial.

In [9]:
nowcast = xsnow.read(f"{datapath}/smets/gridded/nowcast")
nowcast_forecast = nowcast.append_latest(f"{datapath}/smets/gridded/forecast")

[i] xsnow.xsnow_io: Appended 58 new timestamps: 2024-01-31T03:00:00--2024-02-02T12:00:00


## 2. Lazy versus eager loading
When reading large datasets into the `xsnow` gridded data structure, it’s important to understand the difference between lazy and eager loading — and how this affects memory usage.

 * <u>Eager loading</u> means: as soon as you call the read function, the **entire dataset is loaded into memory** (i.e., into a concrete `xr.Dataset`). Further operations are applied on that in-memory object.

 * <u>Lazy loading</u> means: the read function returns a deferred object (or a data structure with deferred chunks) that **doesn’t immediately load all data**. You can continue chaining selections/transformations, and only when you trigger a final compute will the data actually be read from disk and loaded into memory.

For more information, see [Handling large datasets](./lazy_analysis). 

## 3. Subsetting data while reading

As a convenience, the dataset can already be subset during the call to `read()`. The entire dataset is being parsed first, and then subset to the desired coordinates. This is particularly powerful if you load your data **lazily** first---*"load only what you need"*. For example:


In [10]:
subset = xsnow.read(f"{datapath}/pros/gridded/", 
                location=['VIR1A', 'VIR3A'],
                slope={'inclination': 38, 'azimuth': 180},
                time=slice('2024-01-16T10:00', '2024-01-16T12:00'),
                lazy=True)

[i] xsnow.xsnow_io: Using lazy loading with Dask
[i] xsnow.xsnow_io: Creating lazy datasets backed by dask arrays...
[i] xsnow.xsnow_io: Data will NOT be computed until explicitly requested by user
[i] xsnow.xsnow_io: Created 25 lazy datasets (data NOT yet loaded into memory)


## 4. Inspecting structure and metadata
You can use standard xarray accessors to explore shape and metadata:

In [11]:
# List dimensions and sizes
xs.sizes

Frozen({'location': 1, 'time': 416, 'slope': 1, 'realization': 1, 'layer': 12})

In [12]:
# List coordinates and their info
xs.coords

Coordinates:
    altitude     (location) float64 8B 2.372e+03
    latitude     (location) float64 8B 47.15
  * location     (location) <U5 20B 'VIR1A'
    longitude    (location) float64 8B 11.19
  * time         (time) datetime64[ns] 3kB 2024-01-16T05:00:00 ... 2024-02-02...
    azimuth      (slope) float64 8B 0.0
    inclination  (slope) float64 8B 0.0
  * slope        (slope) int64 8B 0
  * realization  (realization) int64 8B 0
  * layer        (layer) int64 96B 0 1 2 3 4 5 6 7 8 9 10 11
    z            (location, time, slope, realization, layer) float32 20kB 0.0...

In [13]:
# List all data variables
xs.data_vars

Data variables:
    air_content               (location, time, slope, realization, layer) float32 20kB ...
    bond_size                 (location, time, slope, realization, layer) float32 20kB ...
    coord_number              (location, time, slope, realization, layer) float32 20kB ...
    dendricity                (location, time, slope, realization, layer) float32 20kB ...
    density                   (location, time, slope, realization, layer) float32 20kB ...
    element_ID                (location, time, slope, realization, layer) float32 20kB ...
    grain_size                (location, time, slope, realization, layer) float32 20kB ...
    grain_type                (location, time, slope, realization, layer) float32 20kB ...
    gs_difference             (location, time, slope, realization, layer) float32 20kB ...
    hand_hardness             (location, time, slope, realization, layer) float32 20kB ...
    hardness_difference       (location, time, slope, realization, layer) 

Inspect individual variables (e.g., snow density):

In [14]:
print(xs['density'])

<xarray.DataArray 'density' (location: 1, time: 416, slope: 1, realization: 1,
                             layer: 12)> Size: 20kB
array([[[[[  nan,   nan,   nan, ...,   nan,   nan,   nan]]],


        [[[  nan,   nan,   nan, ...,   nan,   nan,   nan]]],


        [[[  nan,   nan,   nan, ...,   nan,   nan,   nan]]],


        ...,


        [[[213.9, 209. , 223.7, ..., 171.9, 142.4, 124.9]]],


        [[[214. , 209.2, 223.7, ..., 172.6, 143. , 125. ]]],


        [[[214.2, 209.3, 223.8, ..., 173.3, 143.6, 125. ]]]]],
      shape=(1, 416, 1, 1, 12), dtype=float32)
Coordinates:
    altitude     (location) float64 8B 2.372e+03
    latitude     (location) float64 8B 47.15
  * location     (location) <U5 20B 'VIR1A'
    longitude    (location) float64 8B 11.19
  * time         (time) datetime64[ns] 3kB 2024-01-16T05:00:00 ... 2024-02-02...
    azimuth      (slope) float64 8B 0.0
    inclination  (slope) float64 8B 0.0
  * slope        (slope) int64 8B 0
  * realization  (realization) int64

Each variable carries **attributes (metadata)** like units and descriptions.

View dataset- and variable-level attributes:

In [15]:
# dataset attributes
xs.attrs

{'Conventions': 'CF-1.8', 'crs': 'EPSG:4326'}

In [16]:
# variable-level attributes
xs['density'].attrs

{'standard_name': 'mass_density_of_snow',
 'units': 'kg m-3',
 'long_name': 'mass density of snow'}

## 5. Adding or modifying metadata

Metadata are stored under `.attrs`. You can freely edit or add entries.

For example, add a comment:

In [17]:
xs.attrs['comments'] = 'You can document your thoughts!'
xs.attrs

{'Conventions': 'CF-1.8',
 'crs': 'EPSG:4326',
 'comments': 'You can document your thoughts!'}

Modify variable-level attributes, e.g., change units or add remarks:

In [18]:
xs['density'].attrs['comment'] = "What's the density of ice cream?"
xs['density'].attrs

{'standard_name': 'mass_density_of_snow',
 'units': 'kg m-3',
 'long_name': 'mass density of snow',
 'comment': "What's the density of ice cream?"}

You could record processing steps in a `history` attribute:

In [19]:
from datetime import datetime
history_line = f"{datetime.now().isoformat(timespec='seconds')}: modified metadata interactively"
xs.attrs['history'] = xs.attrs.get('history', '') + '\n' + history_line
print(xs.attrs['history'])


2025-12-16T13:39:50: modified metadata interactively


## 6. Writing datasets to file

You can save your `xsnowDataset` back to file(s). To learn about supported formats, explore the `to_*()` methods in the [xsnow_io](../api/_generated/xsnow.xsnow_io) module API docs. For example,

- `to_netcdf()`: An almost exact dump of the `xsnowDataset` that can be parsed again by `read()`.
- `to_pro()` and `to_smet()`: For every (location, time, slope, realization) you can write one `.smet` and `.pro` file.

First, create a temporary directory to write to:

In [20]:
import tempfile
tmpdir = tempfile.mkdtemp(prefix="xsnow-demo-")

### Writing to .pro / .smet

In [21]:
# Write a single profile timeseries to .pro/.smet
xs.to_pro(f"{tmpdir}/test.pro")
xs.to_smet(f"{tmpdir}/test.smet")

### Dumping the entire dataset to NetCDF

In [22]:
xs.to_netcdf(f"{tmpdir}/test.nc")

[i] xsnow.xsnow_io: Dataset successfully saved to /tmp/xsnow-demo-se9hdh51/test.nc
